In [1]:
from IPython import get_ipython
import traceback
import datetime
import os
import geopandas as gpd
import pandas as pd
import numpy as np
import json
import h3
import folium
import osmnx as ox
from shapely import wkt
from folium.plugins import HeatMap
from shapely.geometry import Polygon

print(datetime.datetime.now())
VISUALIZATION = True
GEXAGON_RES = 11

folder_for_data = os.path.join('.')

df_data = pd.read_csv(
    os.path.join(folder_for_data, 'datasetfines.csv'))

2023-01-29 21:19:09.400000


Выведем немного статистики

In [2]:
print('\n head()')
print(df_data.head().to_string())
print('\ndescribe()')
print(df_data.describe())
print('\ninfo()')
print(df_data.info())


 head()
            Период        ДатаНачала     ДатаОкончания      Широта1     Долгота1      Широта2     Долгота2  УчастокДороги    sec
0  27.12.2022 0:00  27.12.2022 14:01  27.12.2022 15:31    55,796806    49,124533     55,79675    49,124521            110  24704
1  27.12.2022 0:00  27.12.2022 14:01  27.12.2022 14:44  55,77725317  49,14167833  55,77726917  49,14164883            140  60274
2  27.12.2022 0:00  27.12.2022 14:01  27.12.2022 14:30  55,77713333  49,14193117    55,777121    49,142008            140   2893
3  27.12.2022 0:00  27.12.2022 14:01  27.12.2022 14:30  55,77709467  49,14201633  55,77706133  49,14213133            140    534
4  27.12.2022 0:00  27.12.2022 14:03  27.12.2022 14:56    55,797693  49,13365367  55,79768983  49,13369267            112  70546

describe()
       УчастокДороги            sec
count  177845.000000  177845.000000
mean      137.891681   47408.554826
std        23.049412   27515.504906
min       101.000000       0.000000
25%       116.000000   23

Исходя из статистики сверху видно, что в таблице отсутствуют Nan значения

Далее проверим наличие дубликатов в данных и приналичии удалим их

In [3]:
len_df_data = len(df_data)
df_data.drop_duplicates(inplace=True)
print(f'Было удалено {len_df_data - len(df_data)} дубликатов')

# Удаление переменных, которые больше не будут использоваться
# (чтобы они больше не отвлекали меня)
del len_df_data


Было удалено 0 дубликатов


Преобразовываем в столцов с датой в TimeStamp
А с числами в числа

In [4]:
# Для колонок с датами
for column_name in ['Период', 'ДатаНачала', 'ДатаОкончания']:
    df_data[column_name] = pd.to_datetime(
        df_data[column_name],
        format='%d.%m.%Y %H:%M')

# Для float колонок
for column_name in ['Широта1', 'Широта2', 'Долгота1', 'Долгота2']:
    df_data[column_name] = df_data[column_name].str.replace(',', '.')
    df_data[column_name] = df_data[column_name].astype(float)


Минимально необходимое количество деуйствий выполнено для постоения heatmap,
поэтому построим карту совмещённую с heatmap
Для этого бдем использовать Широта1, Долгота1

In [5]:
from geopy.geocoders import Nominatim
import time
from folium import branca


def get_location_by_address(address):
    """This function returns a location as raw from an address
    will repeat until success"""
    time.sleep(1)
    try:
        return app.geocode(address).raw
    except:
        return get_location_by_address(address)


app = Nominatim(user_agent="test_task")
location = get_location_by_address("Kazan")

city_boundingbox = np.array(location['boundingbox'], dtype=np.float32)
middle_of_city = [np.mean(city_boundingbox[:2]),
                  np.mean(city_boundingbox[2:4])]

my_map = folium.Map(location=middle_of_city, zoom_start=11)
points_for_heatmap = list(zip(list(df_data['Широта1']),
                              list(df_data['Долгота1'])))

accidents = folium.FeatureGroup(name='Аварии')
my_heat_map = HeatMap(points_for_heatmap)

my_heat_map.add_to(accidents)
accidents.add_to(my_map)
folium.LayerControl().add_to(my_map)
colormap = branca.colormap.LinearColormap(
    ["#4efddf", "#edff35", "#fa8112", "#ff0300"],
    vmin=0, vmax=1, caption="Intensity")
colormap.add_to(my_map)
my_map.save('1. heatmap по авариям.html')
my_map

Так как есть много точек в которых heatmap красный сильно,
то посмотрев на карту решить задачу не получается

Есть несколько решений данной задачи:
1. Простой вариант решения -
посмотреть на каких участках дороги наибольшее количество аварий произошло


In [6]:
print(df_data['УчастокДороги'].value_counts())

147    12311
155     9723
156     9379
114     8431
171     7211
       ...  
181       50
185       41
196       40
182       28
189       26
Name: УчастокДороги, Length: 90, dtype: int64


По итогам вывода видно, что наибольшее количество аварий
произошло на 147 участке дороги с количеством аварий: 12311

На втором месте находится участок дороги 155 с количеством аварий: 9723

Так как тестовое задание решалось на выходных и
было бы нехорошо спрашивать достаточно ли решения выше или нет,
поэтому ещё сделал вариант посложнее

2. Сложный вариант<br>
Было решено поделить карту Казани на сектора, а в качестве формы сектора
изначально использовался квадрат,
но исходя из [видео от Uber по геоаналитике](https://www.youtube.com/watch?v=ay2uwtRO3QE)
было принято решение использовать гексагоны, поделив Казань на гексагоны

Посмотрим как выглядит гексагон в географическом центре Казани

Масштаб гексагонов можно регулировать дополнительная информация на
[сайте](https://h3geo.org/docs/core-library/restable/)

In [7]:
def visualize_hexagons(hexagons, color="red", folium_map=None):
    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v: v[0], polyline))
        lng.extend(map(lambda v: v[1], polyline))
        polylines.append(polyline)

    if folium_map is None:
        m = folium.Map(location=[sum(lat) / len(lat), sum(lng) / len(lng)],
                       zoom_start=13, tiles='cartodbpositron')
    else:
        m = folium_map

    for polyline in polylines:
        my_PolyLine = folium.PolyLine(locations=polyline, weight=10,
                                      color=color)
        m.add_child(my_PolyLine)
    if VISUALIZATION:
        return m
    else:
        return None


h3_address = h3.geo_to_h3(middle_of_city[0], middle_of_city[1],
                          9)  # 9 - индекс, определяющий размер гексагона
visualize_hexagons([h3_address])

Теперь, с помощью osmnx и h3 сгенерим гексагоны внутри полигона г. Казань:

1) Выгрузим границы Казани из OSM

In [8]:
import datetime


def visualize_polygons(geometry):
    lats, lons = get_lat_lon(geometry)

    m = folium.Map(location=[sum(lats) / len(lats), sum(lons) / len(lons)],
                   zoom_start=9, tiles='cartodbpositron')

    overlay = gpd.GeoSeries(geometry).to_json()
    folium.GeoJson(overlay, name='boundary').add_to(m)
    m.save('2. Выделенная область для гексагонов.html')
    if VISUALIZATION:
        return m
    else:
        return None


# выводим центроиды полигонов
def get_lat_lon(geometry):
    lon = geometry.apply(lambda x: x.x if x.type == 'Point' else x.centroid.x)
    lat = geometry.apply(lambda x: x.y if x.type == 'Point' else x.centroid.y)
    return lat, lon


# выгрузим границы Казани из OSM
cities = ['Казань']
print(datetime.datetime.now())
polygon_krd = ox.geometries_from_place(cities, {
    'boundary': 'administrative'}).reset_index()
print(datetime.datetime.now())
polygon_krd = polygon_krd[(polygon_krd['name'] == 'городской округ Казань')]
# посмотрим что получилось
visualize_polygons(polygon_krd['geometry'])

2023-01-29 21:19:16.299000


C:\ProgramData\Anaconda3\envs\test_task_muchammad\lib\site-packages\osmnx\geocoder.py:110: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  gdf = gdf.append(_geocode_query_to_gdf(q, wr, by_osmid))
C:\ProgramData\Anaconda3\envs\test_task_muchammad\lib\site-packages\osmnx\utils_geo.py:335: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  for polygon in geometry:
C:\ProgramData\Anaconda3\envs\test_task_muchammad\lib\site-packages\osmnx\geometries.py:805: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  for merged_outer_linestring in list(merged_outer_linestrings):
C:\ProgramData\Anaconda3\envs

2023-01-29 21:19:18.582000


2) Сгенерим гексагоны внутри полигона

In [9]:

def create_hexagons(geoJson):
    polyline = geoJson['coordinates'][0]

    polyline.append(polyline[0])
    lat = [p[0] for p in polyline]
    lng = [p[1] for p in polyline]
    m = folium.Map(location=[sum(lat) / len(lat), sum(lng) / len(lng)],
                   zoom_start=9, tiles='cartodbpositron')
    my_PolyLine = folium.PolyLine(locations=polyline, weight=8, color="green")
    m.add_child(my_PolyLine)

    hexagons = list(h3.polyfill(geoJson, GEXAGON_RES))
    polylines = []
    lat = []
    lng = []
    for hex in hexagons:
        polygons = h3.h3_set_to_multi_polygon([hex], geo_json=False)
        # flatten polygons into loops.
        outlines = [loop for polygon in polygons for loop in polygon]
        polyline = [outline + [outline[0]] for outline in outlines][0]
        lat.extend(map(lambda v: v[0], polyline))
        lng.extend(map(lambda v: v[1], polyline))
        polylines.append(polyline)
    for polyline in polylines:
        my_PolyLine = folium.PolyLine(locations=polyline, weight=3,
                                      color='red')
        m.add_child(my_PolyLine)

    polylines_x = []
    for j in range(len(polylines)):
        a = np.column_stack((np.array(polylines[j])[:, 1],
                             np.array(polylines[j])[:, 0])).tolist()
        polylines_x.append([(a[i][0], a[i][1]) for i in range(len(a))])

    polygons_hex = pd.Series(polylines_x).apply(lambda x: Polygon(x))

    return m, polygons_hex, polylines


# polygon_hex , polylines - геометрии гексагонов в разных форматах
print(datetime.datetime.now())
# сгенерим гексагоны внутри полигона г. Казань
geoJson = json.loads(gpd.GeoSeries(polygon_krd['geometry']).to_json())
geoJson = geoJson['features'][0]['geometry']
geoJson = {'type': 'Polygon', 'coordinates': [
    np.column_stack((np.array(geoJson['coordinates'][0])[:, 1],
                     np.array(geoJson['coordinates'][0])[:, 0])).tolist()]}

m, polygons, polylines = create_hexagons(geoJson)
m.save('3. Казань в гексагонах.html')
# m

2023-01-29 21:19:18.681000


Далее нам надо поместить точки аварий в наши сгенерированные гексагоны

In [10]:
# sjoin - spatial join - пересекаем гексагоны с объектами
# (определяем какие объекты находятся в разрезе каждого гексагона)

gdf_1 = gpd.GeoDataFrame(df_data, geometry=gpd.points_from_xy(df_data.Долгота1,
                                                              df_data.Широта1))

gdf_2 = pd.DataFrame(polygons, columns=['geometry'])
gdf_2['polylines'] = polylines
gdf_2['geometry'] = gdf_2['geometry'].astype(str)
geometry_uniq = pd.DataFrame(gdf_2['geometry'].drop_duplicates())
geometry_uniq['id'] = np.arange(len(geometry_uniq)).astype(str)

C:\ProgramData\Anaconda3\envs\test_task_muchammad\lib\site-packages\geopandas\array.py:275: ShapelyDeprecationWarning: The array interface is deprecated and will no longer work in Shapely 2.0. Convert the '.coords' to a numpy array instead.
  return GeometryArray(vectorized.points_from_xy(x, y, z), crs=crs)


In [11]:
gdf_2 = gdf_2.merge(geometry_uniq, on='geometry')
gdf_2['geometry'] = gdf_2['geometry'].apply(wkt.loads)
gdf_2 = gpd.GeoDataFrame(gdf_2, geometry='geometry')


In [12]:
itog_table = gpd.sjoin(gdf_2, gdf_1, how='left', op='intersects')
# itog_table.loc[pd.isna(itog_table["УчастокДороги"]), :].index
itog_table = itog_table.dropna()
itog_table.head()

geometry  \
223  POLYGON ((49.15467 55.82237, 49.15500 55.82218...   
223  POLYGON ((49.15467 55.82237, 49.15500 55.82218...   
223  POLYGON ((49.15467 55.82237, 49.15500 55.82218...   
223  POLYGON ((49.15467 55.82237, 49.15500 55.82218...   
223  POLYGON ((49.15467 55.82237, 49.15500 55.82218...   

                                             polylines   id  index_right  \
223  [(55.822371176335196, 49.15467451044702), (55....  223      82352.0   
223  [(55.822371176335196, 49.15467451044702), (55....  223     161180.0   
223  [(55.822371176335196, 49.15467451044702), (55....  223     169251.0   
223  [(55.822371176335196, 49.15467451044702), (55....  223     121598.0   
223  [(55.822371176335196, 49.15467451044702), (55....  223     155382.0   

        Период          ДатаНачала       ДатаОкончания    Широта1   Долгота1  \
223 2022-02-01 2022-02-01 11:04:00 2022-02-01 12:11:00  55.822658  49.155331   
223 2022-11-22 2022-11-22 09:05:00 2022-11-22 10:34:00  55.822616  49.155407   
223 2022-12-02 2022-12-02 09:36:00 2022-12-02 10:18:00  55.822616  49.155403   
223 2022-06-28 2022-06-28 11:05:00 2022-06-28 11:46:00  55.822618  49.155387   
223 2022-11-17 2022-11-17 11:08:00 2022-11-17 11:48:00  55.822618  49.155351   

       Широта2   Долгота2  УчастокДороги      sec  
223  55.822666  49.155350          176.0  60722.0  
223  55.822578  49.155412          176.0  50983.0  
223  55.822619  49.155443          176.0  61645.0  
223  55.822570  49.155368          176.0  30854.0  
223  55.822582  49.155369          176.0  49729.0

Исходя из данных можно сделать вывод, что часть аварий
находится за пределами Казани

In [13]:
def create_choropleth(data, json, columns, legend_name, feature, bins):
    lat, lon = get_lat_lon(data['geometry'])

    m = folium.Map(location=[sum(lat) / len(lat), sum(lon) / len(lon)],
                   zoom_start=13, tiles='cartodbpositron')

    folium.Choropleth(
        geo_data=json,
        name="choropleth",
        data=data,
        columns=columns,
        key_on="feature.id",
        fill_color="YlGn",
        fill_opacity=0.7,
        line_opacity=0.2,
        legend_name=legend_name,
        nan_fill_color='black',
        bins=bins

    ).add_to(m)

    folium.LayerControl().add_to(m)
    return m


# подготовим данные
itog_table['geometry'] = itog_table['geometry'].astype(str)  # для groupby
itog_table['id'] = itog_table['id'].astype(str)  # для Choropleth

C:\ProgramData\Anaconda3\envs\test_task_muchammad\lib\site-packages\geopandas\geodataframe.py:1321: UserWarning: Geometry column does not contain geometry.
  warnings.warn("Geometry column does not contain geometry.")


In [14]:
agg_all = itog_table.groupby(['geometry', 'id'], as_index=False).agg(
    {'Широта1': 'count'}).rename(columns={'Широта1': 'counts'})
agg_all['geometry'] = agg_all['geometry'].apply(
    wkt.loads)  #возвращаем формат геометрий

Выведем в каком гексагоне больше всего аварий

In [15]:
print(agg_all.sort_values(by='counts', ascending=False))

                                              geometry      id  counts
32   POLYGON ((49.10123678346601 55.81884652122972,...   95260    2677
31   POLYGON ((49.10123678346601 55.81884652122972,...  151382    1749
456  POLYGON ((49.12439611293262 55.79616079856067,...  149223    1703
370  POLYGON ((49.11854753541169 55.8168238648454, ...  201153    1695
884  POLYGON ((49.15536265100908 55.7898410026218, ...   55178    1679
..                                                 ...     ...     ...
262  POLYGON ((49.11408853719833 55.81706871354889,...  172591       1
797  POLYGON ((49.14605463839147 55.78955073524688,...   96238       1
270  POLYGON ((49.11442660801577 55.78544060654043,...  232042       1
275  POLYGON ((49.11460398818744 55.78330874157297,...  208308       1
0    POLYGON ((49.08908823422412 55.81953581763454,...  234768       1

[943 rows x 3 columns]


В гексагоне с id 95260 наибольшее количество аварий произошло

In [19]:
data_geo_1 = gpd.GeoSeries(agg_all.set_index('id')["geometry"]).to_json()

m = create_choropleth(agg_all, data_geo_1, ["id", "counts"],
                      'Number of accidents',
                      'counts', 5)
m.save(
    f'4. Отображение гексагонов на Казань gexagon_resolution={GEXAGON_RES}.html')
m

Отобразим топ 3 точки

In [28]:
top_3 = agg_all.sort_values(by='counts', ascending=False).reset_index()
top_3 = top_3[:3]

data_geo_2 = gpd.GeoSeries(top_3.set_index('id')["geometry"]).to_json()

m = create_choropleth(top_3, data_geo_2, ["id", "counts"],
                      'Number of accidents',
                      'counts', 5)
m.save(f'5. Топ 3 гексагонов на Казань gexagon_resolution={GEXAGON_RES}.html')
m

In [17]:
# Дополнительный анализ
print(df_data['Период'].dt.day_name().value_counts())


Wednesday    37003
Thursday     36844
Tuesday      35717
Friday       34594
Monday       33687
Name: Период, dtype: int64


Бывают случаи, когда большое количество аварий расположено
на пересечении двух гексагонов, поэтому
наиболее логично делить карту на гексагоны,
используя разный масштаб<br>

В ходе эксперимемнтов были исследованы разные варианты масштаба
гексагональной сетки, в итоге был выбран масштаб сетки - 11
(эквивалентно 237 279 209 162 гексагонов на всей поверхности земли).

Данных код, при необходимости, позволяет изменять масштаб гексагона.

Итоги:
1. В ходе проведения мною анализа предоставленных данных, вызывает
сомнения актуальность этих данных применительно ко всей
территории Казани, потому что предоставленные данные не охватывают всю Казань,
а в основном охватывают центр.
<br>Среди данных нет информации по окраинным районам.
2. Данные предоставлены только по будним дням, хотя аварии бывают и в выходные
3. Самая аварийная точка при GEXAGON_RES=11 вышла Чистопольская 5

Первично я провёл исследования исспользовав инструмент heatmap и понял,
что этот хороший инструмент для цветовой визуализации данных наложенных на
карту, но он не позволяет вывести измеримые параметры для конкретного участка.

Так как задание включает поиск точки наибольшей концентрации аварий, то было
произведено 2 анализа:<br>
1. Простой - анализ того насколько часто были аварии
на конкретном участке дороги
2. Сложный - Казань была разбита на участки гексагональной формы
и были отображены цветом, только те гексагоны где были по предоставленным данным,
исходя из цвета гексагона можно понять на
каком участке сколько аварий произошло

Вывод: Если есть требование  актуализировать на всю Казань,
то исходные данные требуют актуализации.

